In [28]:
import pandas as pd
import re

In [ ]:
import csv
import requests
hash = "QmR8etyW3TPFadNtNrW54vfnFqmh8vBrMARWV76EmxCZyk"
ipfs_address = "https://gateway.autonolas.tech/ipfs/"

accuracy_link= ipfs_address + hash
response = requests.get(accuracy_link)
print(response)


In [26]:
from io import StringIO
accuracy_store = {}
data = StringIO(response.text)
csv_reader = csv.reader(data, delimiter=',')
for row in csv_reader:
    if row[0] == "tool":
        print(f"headers = {row}")
        continue
    accuracy_store[row[0]] = [
        row[2],
        row[1],
    ]

headers = ['tool', 'tool_accuracy', 'total_requests', 'min', 'max']


In [27]:
print(accuracy_store)

{'claude-prediction-offline': ['481', '57.380457380457386'], 'claude-prediction-online': ['1055', '61.137440758293835'], 'prediction-offline': ['4465', '67.41321388577828'], 'prediction-offline-sme': ['61', '70.49180327868852'], 'prediction-online': ['9490', '66.00632244467862'], 'prediction-online-sme': ['14642', '65.67408823931157'], 'prediction-request-rag': ['2691', '63.58231140839836'], 'prediction-request-rag-claude': ['7428', '65.64351103931072'], 'prediction-request-reasoning': ['17372', '67.11374625834677'], 'prediction-request-reasoning-claude': ['2470', '66.72064777327935'], 'prediction-url-cot-claude': ['1596', '61.904761904761905']}


In [2]:
fpmms = pd.read_parquet('../data/fpmms.parquet')
tools = pd.read_parquet('../data/tools.parquet')
trades = pd.read_parquet('../data/all_trades_profitability.parquet')

In [3]:
INC_TOOLS = [
    "prediction-online",
    "prediction-offline",
    "claude-prediction-online",
    "claude-prediction-offline",
    "prediction-offline-sme",
    "prediction-online-sme",
    "prediction-request-rag",
    "prediction-request-reasoning",
    "prediction-url-cot-claude",
    "prediction-request-rag-claude",
    "prediction-request-reasoning-claude",
]

In [4]:
tools_inc = tools[tools['tool'].isin(INC_TOOLS)]
# filtering errors
tools_non_error = tools_inc[tools_inc['error'] != 1]
tools_non_error.loc[:, 'currentAnswer'] = tools_non_error['currentAnswer'].replace({'no': 'No', 'yes': 'Yes'})
tools_non_error = tools_non_error[tools_non_error['currentAnswer'].isin(['Yes', 'No'])]
tools_non_error = tools_non_error[tools_non_error['vote'].isin(['Yes', 'No'])]
tools_non_error['win'] = (tools_non_error['currentAnswer'] == tools_non_error['vote']).astype(int)
tools_non_error.columns = tools_non_error.columns.astype(str)
wins = tools_non_error.groupby(['tool', 'win']).size().unstack().fillna(0)
wins['tool_accuracy'] = (wins[1] / (wins[0] + wins[1])) * 100
wins.reset_index(inplace=True)
wins['total_requests'] = wins[0] + wins[1]
wins.columns = wins.columns.astype(str)
wins = wins[["tool", "tool_accuracy", "total_requests"]]
wins

win                                 tool  tool_accuracy  total_requests
0              claude-prediction-offline      66.308244             279
1               claude-prediction-online      58.914027            1105
2                     prediction-offline      67.717915            2283
3                 prediction-offline-sme      55.555556              18
4                      prediction-online      65.459066            5631
5                  prediction-online-sme      67.417656            8167
6                 prediction-request-rag      64.217072            1769
7          prediction-request-rag-claude      69.554566            4490
8           prediction-request-reasoning      68.813594            9828
9    prediction-request-reasoning-claude      68.910256            2184
10             prediction-url-cot-claude      64.584980            1265

In [8]:
tools_inc = tools[tools['tool'].isin(INC_TOOLS)]
# filtering errors
tools_non_error = tools_inc[tools_inc['error'] != 1]
tools_non_error.loc[:, 'currentAnswer'] = tools_non_error['currentAnswer'].replace({'no': 'No', 'yes': 'Yes'})
tools_non_error = tools_non_error[tools_non_error['currentAnswer'].isin(['Yes', 'No'])]
tools_non_error = tools_non_error[tools_non_error['vote'].isin(['Yes', 'No'])]
tools_non_error['win'] = (tools_non_error['currentAnswer'] == tools_non_error['vote']).astype(int)
tools_non_error.columns = tools_non_error.columns.astype(str)
timeline = tools_non_error.groupby(['tool'])["request_time"].agg(["min","max"])
timeline

min                  max
tool                                                                         
claude-prediction-offline            2024-04-23 13:09:30  2024-06-10 00:31:30
claude-prediction-online             2024-04-12 12:24:20  2024-06-09 21:41:20
prediction-offline                   2024-04-12 12:20:10  2024-06-08 23:45:00
prediction-offline-sme               2024-04-16 07:58:45  2024-04-29 20:45:15
prediction-online                    2024-04-16 05:52:40  2024-06-09 21:47:20
prediction-online-sme                2024-04-12 11:51:30  2024-06-10 00:06:00
prediction-request-rag               2024-04-12 11:39:40  2024-06-09 21:17:45
prediction-request-rag-claude        2024-04-12 11:14:30  2024-06-07 11:42:30
prediction-request-reasoning         2024-04-12 11:57:05  2024-06-09 21:50:45
prediction-request-reasoning-claude  2024-04-12 11:53:55  2024-06-05 05:00:10
prediction-url-cot-claude            2024-04-12 11:37:15  2024-06-05 05:21:10

In [10]:
total = wins.merge(timeline,how="left", on="tool")
total

tool  tool_accuracy  total_requests  \
0             claude-prediction-offline      66.308244             279   
1              claude-prediction-online      58.914027            1105   
2                    prediction-offline      67.717915            2283   
3                prediction-offline-sme      55.555556              18   
4                     prediction-online      65.459066            5631   
5                 prediction-online-sme      67.417656            8167   
6                prediction-request-rag      64.217072            1769   
7         prediction-request-rag-claude      69.554566            4490   
8          prediction-request-reasoning      68.813594            9828   
9   prediction-request-reasoning-claude      68.910256            2184   
10            prediction-url-cot-claude      64.584980            1265   

                    min                  max  
0   2024-04-23 13:09:30  2024-06-10 00:31:30  
1   2024-04-12 12:24:20  2024-06-09 21:41:20  
2   2024-04-12 12:20:10  2024-06-08 23:45:00  
3   2024-04-16 07:58:45  2024-04-29 20:45:15  
4   2024-04-16 05:52:40  2024-06-09 21:47:20  
5   2024-04-12 11:51:30  2024-06-10 00:06:00  
6   2024-04-12 11:39:40  2024-06-09 21:17:45  
7   2024-04-12 11:14:30  2024-06-07 11:42:30  
8   2024-04-12 11:57:05  2024-06-09 21:50:45  
9   2024-04-12 11:53:55  2024-06-05 05:00:10  
10  2024-04-12 11:37:15  2024-06-05 05:21:10

In [15]:
total.to_csv("accuracy_info.csv")

In [3]:
def extract_question(text):
    pattern = r'"([^"]+\?)"'
    match = re.search(pattern, text)
    if match:
        return match.group(1)
    return text

In [4]:
def get_current_answer(q):
    return trades[trades['title'] == q]['current_answer'].unique()

In [5]:
# only select trades in May 2024
trades['creation_timestamp'] = pd.to_datetime(trades['creation_timestamp'])
trades = trades[trades['creation_timestamp'].dt.month == 5]
trades = trades[trades['creation_timestamp'].dt.year == 2024]

# make a column for winning_vote
tools['winning_vote'] = (tools['vote'] == tools['currentAnswer'])
tools = tools[tools['tool']!= 'resolve-market-reasoning-gpt-4'].reset_index(drop=True)

In [6]:
tools['prompt_request'] = tools['prompt_request'].apply(extract_question)

In [7]:
trades_grouped = trades.groupby(['title', 'winning_trade']).size().unstack().fillna(0)

In [8]:
winning_trades_percentage = trades_grouped[True] / trades_grouped.sum(axis=1)
winning_trades_percentage = winning_trades_percentage.reset_index()
winning_trades_percentage.columns = ['title', 'winning_trade_percentage']
winning_trades_percentage['num_trades'] = list(trades_grouped.sum(axis=1).values)
winning_trades_percentage_bottom_50 = winning_trades_percentage.sort_values(by='winning_trade_percentage', ascending=False)[-50:].reset_index(drop=True)
winning_trades_percentage_top_50 = winning_trades_percentage.sort_values(by='winning_trade_percentage', ascending=False)[:50].reset_index(drop=True)

In [13]:
# winning_trades_percentage.sort_values(by='winning_trade_percentage', ascending=False).reset_index(drop=True).to_csv('winning_trades_percentage.csv', index=False)

In [18]:
winning_trades_percentage_top_50['title'].tolist()



['Will Kylian Mbappe leave Paris St-Germain at the end of the season by 16 May 2024?',
 'Will BlizzCon be reinstated on or by 1 May 2024 after its cancellation in 2024?',
 'Will Joe Biden approve more weapons for Ukraine by 4 May 2024?',
 "Will FiiO's new custom in-ear monitors become the top-selling wireless earbuds by 9 May 2024?",
 'Will Mohamed Salah leave Liverpool on 7 May 2024?',
 "Will Ryan Gosling accept a 'dark' role in a film by 14 May 2024?",
 'Will the Philadelphia 76ers win the NBA play-offs on 7 May 2024?',
 'Will the Panamanian presidential election result in a clear victor by 12 May 2024?',
 'Will the Museum of Old and New Art in Tasmania be allowed to keep its exhibit women-only by 14 May 2024?',
 "Will Diego Maradona's 'Stolen' Golden Ball be auctioned off on 14 May 2024?",
 'Will the Mercedes G-Wagen release an electric version on 1 May 2024?',
 'Will the Israeli government lift the broadcast ban on Al Jazeera on or before 13 May 2024?',
 'Will Intel release its Cor

In [17]:
winning_trades_percentage_bottom_50['title'].tolist()

["Will 'Scavengers Reign' be renewed for a second season on Netflix by 19 May 2024?",
 'Will Fiona Harvey officially file a lawsuit against Netflix and Richard Gadd by 17 May 2024?',
 'Will the final report on the Baltimore bridge collapse be released by 20 May 2024?',
 'Will the Autonomous Racing League successfully hold their second race by May 3, 2024?',
 'Will Trent Staggs win the Senatorial race to replace Sen. Mitt Romney (R-UT) on 5 May 2024?',
 'Will the Houston area experience flooding conditions on 11 May 2024?',
 "Will 'Wednesday' season 2 be released on Netflix by 1 May 2024?",
 'Will Arsenal win against Bournemouth in the Premier League match on 12 May 2024?',
 'Will Qualcomm release its Snapdragon X Plus laptop chip by 1 May 2024?',
 "Will Feyenoord's Arne Slot become the new manager of Liverpool by 1 May 2024?",
 'Will the FCC receive additional funding for replacing Huawei gear by 10 May 2024?',
 'Will there be any major cyber attack on an organization using AI before 2

In [62]:
def losing_percentage(q):
    print(f"Losing percentage for: {q}")
    q_losing = tools[tools['prompt_request'].str.contains(q)].groupby(['tool', 'winning_vote']).size().unstack().fillna(0)
    q_losing_perc = q_losing[False] / (q_losing[False] + q_losing[True])
    q_losing_perc = q_losing_perc.reset_index()
    q_losing_perc.columns = ['tool', 'losing_percentage']
    q_losing_perc['num_calls'] = list(q_losing.sum(axis=1).values)
    q_losing_perc = q_losing_perc.sort_values(by='losing_percentage', ascending=False)
    return q_losing_perc

In [63]:
# have confirmed market resolution was correct
losing_percentage(winning_trades_percentage_bottom_50.loc[0, 'title'])

Losing percentage for: Will 'Scavengers Reign' be renewed for a second season on Netflix by 19 May 2024?


tool  losing_percentage  num_calls
0                   prediction-offline           1.000000       40.0
4        prediction-request-rag-claude           1.000000       17.0
7            prediction-url-cot-claude           1.000000        2.0
2                prediction-online-sme           0.656716       67.0
6  prediction-request-reasoning-claude           0.571429        7.0
5         prediction-request-reasoning           0.538462       52.0
3               prediction-request-rag           0.250000        4.0
1                    prediction-online           0.185185       27.0

In [64]:
# have confirmed currentAnswer
losing_percentage(winning_trades_percentage_bottom_50.loc[0, 'title'])

Losing percentage for: Will 'Scavengers Reign' be renewed for a second season on Netflix by 19 May 2024?


tool  losing_percentage  num_calls
0                   prediction-offline           1.000000       40.0
4        prediction-request-rag-claude           1.000000       17.0
7            prediction-url-cot-claude           1.000000        2.0
2                prediction-online-sme           0.656716       67.0
6  prediction-request-reasoning-claude           0.571429        7.0
5         prediction-request-reasoning           0.538462       52.0
3               prediction-request-rag           0.250000        4.0
1                    prediction-online           0.185185       27.0

In [65]:
# have confirmed currentAnswer
losing_percentage(winning_trades_percentage_bottom_50.loc[1, 'title'])

Losing percentage for: Will Fiona Harvey officially file a lawsuit against Netflix and Richard Gadd by 17 May 2024?


tool  losing_percentage  num_calls
7            prediction-url-cot-claude           1.000000        1.0
2                prediction-online-sme           0.977273       44.0
1                    prediction-online           0.975000       40.0
0                   prediction-offline           0.677419       31.0
5         prediction-request-reasoning           0.534483       58.0
4        prediction-request-rag-claude           0.223881       67.0
6  prediction-request-reasoning-claude           0.200000        5.0
3               prediction-request-rag           0.000000        8.0

In [66]:
# have confirmed currentAnswer
losing_percentage(winning_trades_percentage_bottom_50.loc[2, 'title'])

Losing percentage for: Will the final report on the Baltimore bridge collapse be released by 20 May 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline           1.000000        5.0
1             claude-prediction-online           1.000000        1.0
2                   prediction-offline           1.000000       87.0
6        prediction-request-rag-claude           1.000000       25.0
9            prediction-url-cot-claude           1.000000        1.0
3                    prediction-online           0.951220       41.0
8  prediction-request-reasoning-claude           0.833333        6.0
5               prediction-request-rag           0.714286        7.0
7         prediction-request-reasoning           0.437500       48.0
4                prediction-online-sme           0.394366       71.0

In [67]:
# have confirmed currentAnswer
losing_percentage(winning_trades_percentage_bottom_50.loc[3, 'title'])

Losing percentage for: Will the Autonomous Racing League successfully hold their second race by May 3, 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline                1.0        2.0
1                   prediction-offline                1.0       23.0
2                    prediction-online                1.0       14.0
3                prediction-online-sme                1.0       18.0
4               prediction-request-rag                1.0        5.0
5        prediction-request-rag-claude                1.0        8.0
8            prediction-url-cot-claude                1.0        6.0
6         prediction-request-reasoning                0.0       18.0
7  prediction-request-reasoning-claude                0.0        3.0

In [72]:
losing_percentage(winning_trades_percentage_bottom_50.loc[5, 'title'])

Losing percentage for: Will the Houston area experience flooding conditions on 11 May 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline           1.000000        2.0
1             claude-prediction-online           1.000000        6.0
2                   prediction-offline           1.000000       58.0
4                prediction-online-sme           1.000000       39.0
5               prediction-request-rag           1.000000        4.0
8  prediction-request-reasoning-claude           1.000000        8.0
9            prediction-url-cot-claude           1.000000        5.0
6        prediction-request-rag-claude           0.754717       53.0
7         prediction-request-reasoning           0.369048       84.0
3                    prediction-online           0.166667       72.0

In [73]:
losing_percentage(winning_trades_percentage_bottom_50.loc[6, 'title'])

Losing percentage for: Will 'Wednesday' season 2 be released on Netflix by 1 May 2024?


tool  losing_percentage  num_calls
1                prediction-online-sme           0.750000        4.0
5  prediction-request-reasoning-claude           0.750000        4.0
2               prediction-request-rag           0.666667        6.0
3        prediction-request-rag-claude           0.500000        2.0
4         prediction-request-reasoning           0.400000        5.0
0             claude-prediction-online           0.000000        1.0

In [74]:
losing_percentage(winning_trades_percentage_bottom_50.loc[7, 'title'])

Losing percentage for: Will Arsenal win against Bournemouth in the Premier League match on 12 May 2024?


tool  losing_percentage  num_calls
0                   prediction-offline           1.000000       11.0
1                    prediction-online           1.000000       17.0
2                prediction-online-sme           1.000000       30.0
4        prediction-request-rag-claude           1.000000       45.0
5         prediction-request-reasoning           0.874016      127.0
3               prediction-request-rag           0.250000        4.0
6  prediction-request-reasoning-claude           0.000000        2.0

In [75]:
losing_percentage(winning_trades_percentage_bottom_50.loc[8, 'title'])

Losing percentage for: Will Qualcomm release its Snapdragon X Plus laptop chip by 1 May 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline           1.000000        7.0
1                   prediction-offline           1.000000        1.0
3                prediction-online-sme           1.000000       19.0
5        prediction-request-rag-claude           1.000000       15.0
4               prediction-request-rag           0.941176       17.0
2                    prediction-online           0.800000        5.0
7  prediction-request-reasoning-claude           0.666667       15.0
6         prediction-request-reasoning           0.652174       23.0
8            prediction-url-cot-claude           0.333333        3.0

In [76]:
losing_percentage(winning_trades_percentage_bottom_50.loc[9, 'title'])

Losing percentage for: Will Feyenoord's Arne Slot become the new manager of Liverpool by 1 May 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline           1.000000        4.0
1                   prediction-offline           1.000000        2.0
8            prediction-url-cot-claude           1.000000        2.0
6         prediction-request-reasoning           0.916667       12.0
7  prediction-request-reasoning-claude           0.900000       10.0
4               prediction-request-rag           0.714286       14.0
3                prediction-online-sme           0.666667        9.0
2                    prediction-online           0.500000        2.0
5        prediction-request-rag-claude           0.454545       11.0

In [77]:
losing_percentage(winning_trades_percentage_bottom_50.loc[10, 'title'])

Losing percentage for: Will the FCC receive additional funding for replacing Huawei gear by 10 May 2024?


tool  losing_percentage  num_calls
0            claude-prediction-offline           1.000000        6.0
1             claude-prediction-online           1.000000        3.0
2                   prediction-offline           1.000000       36.0
6        prediction-request-rag-claude           1.000000       50.0
4                prediction-online-sme           0.986486       74.0
5               prediction-request-rag           0.947368       19.0
3                    prediction-online           0.910714       56.0
9            prediction-url-cot-claude           0.777778        9.0
7         prediction-request-reasoning           0.465753       73.0
8  prediction-request-reasoning-claude           0.071429       14.0

In [98]:
all_q = winning_trades_percentage_bottom_50['title'].unique().tolist()
q_losing = tools[tools['prompt_request'].isin(all_q)]
q_losing = q_losing.groupby(['tool'])['winning_vote'].value_counts().unstack().fillna(0)
q_losing_perc = q_losing[False] / (q_losing[False] + q_losing[True])
q_losing_perc = q_losing_perc.reset_index()
q_losing_perc.columns = ['tool', 'losing_percentage']
q_losing_perc['num_calls'] = list(q_losing.sum(axis=1).values)
q_losing_perc = q_losing_perc.sort_values(by='losing_percentage', ascending=False)

In [99]:
q_losing_perc

tool  losing_percentage  num_calls
3                prediction-offline-sme           1.000000        2.0
7         prediction-request-rag-claude           0.913007     1184.0
2                    prediction-offline           0.893281     1012.0
6                prediction-request-rag           0.889881      336.0
5                 prediction-online-sme           0.857143     1722.0
4                     prediction-online           0.853553     1154.0
8          prediction-request-reasoning           0.847451     2727.0
10            prediction-url-cot-claude           0.846154      130.0
1              claude-prediction-online           0.735849       53.0
9   prediction-request-reasoning-claude           0.659664      238.0
0             claude-prediction-offline           0.591549      142.0

In [103]:
all_q = winning_trades_percentage_bottom_50['title'].unique().tolist()
q_losing = tools[tools['prompt_request'].isin(all_q)]
q_losing.groupby(['tool'])['confidence'].value_counts().unstack().fillna(0)

confidence                           0.00   0.10   0.20  0.30   0.40   0.50  \
tool                                                                          
claude-prediction-offline             0.0    0.0    5.0  46.0    4.0    0.0   
claude-prediction-online              0.0    0.0    2.0  10.0    7.0    3.0   
prediction-offline                    0.0  267.0    2.0  13.0  302.0  189.0   
prediction-offline-sme                0.0    0.0    0.0   0.0    0.0    0.0   
prediction-online                     0.0   22.0    4.0   5.0   43.0   23.0   
prediction-online-sme                 1.0   27.0   10.0   0.0   71.0    2.0   
prediction-request-rag                0.0    3.0    2.0   0.0    4.0    4.0   
prediction-request-rag-claude         0.0    0.0    1.0  32.0    0.0    0.0   
prediction-request-reasoning          0.0    3.0  103.0   1.0   58.0   97.0   
prediction-request-reasoning-claude   0.0    0.0    0.0   3.0    4.0    0.0   
prediction-url-cot-claude             0.0    2.0    1.0   2.0    0.0    0.0   

confidence                           0.55   0.60   0.65   0.70   0.75   0.80  \
tool                                                                           
claude-prediction-offline             0.0   87.0    0.0    0.0    0.0    0.0   
claude-prediction-online              0.0   30.0    0.0    0.0    0.0    0.0   
prediction-offline                    0.0  231.0    3.0    0.0    0.0    0.0   
prediction-offline-sme                0.0    0.0    0.0    0.0    2.0    0.0   
prediction-online                     8.0  670.0   99.0    2.0   76.0   28.0   
prediction-online-sme                 0.0  679.0  234.0   39.0  149.0   76.0   
prediction-request-rag                0.0   25.0    5.0   48.0   11.0   36.0   
prediction-request-rag-claude         0.0  175.0    0.0  513.0    0.0  209.0   
prediction-request-reasoning          0.0  315.0  176.0  441.0  317.0  339.0   
prediction-request-reasoning-claude   0.0   27.0    0.0   38.0    4.0   76.0   
prediction-url-cot-claude             0.0   40.0    0.0   60.0    0.0   22.0   

confidence                            0.85  0.90  0.95  0.99  1.00  
tool                                                                
claude-prediction-offline              0.0   0.0   0.0   0.0   0.0  
claude-prediction-online               0.0   1.0   0.0   0.0   0.0  
prediction-offline                     1.0   2.0   0.0   0.0   1.0  
prediction-offline-sme                 0.0   0.0   0.0   0.0   0.0  
prediction-online                     55.0  25.0  11.0   0.0  20.0  
prediction-online-sme                109.0  80.0   6.0   0.0  39.0  
prediction-request-rag                57.0  16.0  11.0   1.0  20.0  
prediction-request-rag-claude          3.0  40.0   3.0   0.0   0.0  
prediction-request-reasoning         159.0  44.0  58.0   0.0  97.0  
prediction-request-reasoning-claude    0.0   8.0   1.0   0.0   2.0  
prediction-url-cot-claude              0.0   3.0   0.0   0.0   0.0

In [34]:
def get_question(text: str) -> str:
    """Get the question from a text."""
    # Regex to find text within double quotes
    pattern = r'"([^"]*)"'

    # Find all occurrences
    questions = re.findall(pattern, text)

    # Assuming you want the first question if there are multiple
    question = questions[0] if questions else None

    return question

In [41]:
from web3 import Web3
from typing import Optional
import re
import pickle

def block_number_to_timestamp(block_number: int, web3: Web3) -> str:
    """Convert a block number to a timestamp."""
    block = web3.eth.get_block(block_number)
    timestamp = datetime.utcfromtimestamp(block["timestamp"])
    return timestamp.strftime("%Y-%m-%d %H:%M:%S")


def parallelize_timestamp_conversion(df: pd.DataFrame, function: callable) -> list:
    """Parallelize the timestamp conversion."""
    block_numbers = df["request_block"].tolist()
    with ThreadPoolExecutor(max_workers=10) as executor:
        results = list(
            tqdm(executor.map(function, block_numbers), total=len(block_numbers))
        )
    return results

In [38]:
def current_answer(text: str, fpmms: pd.DataFrame) -> Optional[str]:
    """Get the current answer for a question."""
    row = fpmms[fpmms["title"] == text]
    if row.shape[0] == 0:
        return None
    return row["currentAnswer"].values[0]

In [48]:
from functools import partial
from concurrent.futures import ThreadPoolExecutor
def weekly_analysis():
    rpc = "https://lb.nodies.app/v1/406d8dcc043f4cb3959ed7d6673d311a"
    web3 = Web3(Web3.HTTPProvider(rpc))
    # Get currentAnswer from FPMMS
    fpmms = pd.read_parquet('../data/fpmms.parquet')
    tools = pd.read_parquet('../data/tools.parquet')

    # Get the question from the tools
    print("Getting the question and current answer for the tools")
    tools["title"] = tools["prompt_request"].apply(lambda x: get_question(x))
    tools["currentAnswer"] = tools["title"].apply(lambda x: current_answer(x, fpmms))

    tools["currentAnswer"] = tools["currentAnswer"].str.replace("yes", "Yes")
    tools["currentAnswer"] = tools["currentAnswer"].str.replace("no", "No")

    # Convert block number to timestamp
    print("Converting block number to timestamp")
    t_map = pickle.load(open("../data/t_map.pkl", "rb"))
    tools["request_time"] = tools["request_block"].map(t_map)

    # Identify tools with missing request_time and fill them
    missing_time_indices = tools[tools["request_time"].isna()].index
    if not missing_time_indices.empty:
        partial_block_number_to_timestamp = partial(
            block_number_to_timestamp, web3=web3
        )
        missing_timestamps = parallelize_timestamp_conversion(
            tools.loc[missing_time_indices], partial_block_number_to_timestamp
        )

        # Update the original DataFrame with the missing timestamps
        for i, timestamp in zip(missing_time_indices, missing_timestamps):
            tools.at[i, "request_time"] = timestamp

    tools["request_month_year"] = pd.to_datetime(tools["request_time"]).dt.strftime(
        "%Y-%m"
    )
    tools["request_month_year_week"] = (
        pd.to_datetime(tools["request_time"]).dt.to_period("W").astype(str)
    )

    # Save the tools data after the updates on the content
    tools.to_parquet('../data/tools.parquet', index=False)

    # Update t_map with new timestamps
    new_timestamps = (
        tools[["request_block", "request_time"]]
        .dropna()
        .set_index("request_block")
        .to_dict()["request_time"]
    )
    t_map.update(new_timestamps)

    with open("../data/t_map.pkl", "wb") as f:
        pickle.dump(t_map, f)

    # clean and release all memory
    del tools
    del fpmms
    del t_map
    gc.collect()

    print("Weekly analysis files generated and saved")


In [50]:
import os
import pickle
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
from tqdm import tqdm
from web3 import Web3
import pandas as pd
from pathlib import Path
from functools import partial
weekly_analysis()

Getting the question and current answer for the tools
Converting block number to timestamp


  0%|          | 0/11690 [00:00<?, ?it/s]/var/folders/gp/02mb1d514ng739czlxw1lhh00000gn/T/ipykernel_28372/2484496282.py:9: DeprecationWarning: datetime.datetime.utcfromtimestamp() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.fromtimestamp(timestamp, datetime.UTC).
  timestamp = datetime.utcfromtimestamp(block["timestamp"])
100%|██████████| 11690/11690 [01:40<00:00, 116.87it/s]


NameError: name 'gc' is not defined

In [51]:
import gc
gc.collect()

1187